<a href="https://colab.research.google.com/github/temesgenm/Calculate-Precipitation-based-Agricultural-Drought-Indices-with-Python/blob/master/Floodplain_Land_Use_Change_Python_Based_Tool_updated10_24_2024.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Detection of Floodplain Land Use Change Using Web-based Python Programming**

This pyhon-based tool can map land use change in global floodplains. Floodplain land use change indicates human disturbance in natural floodplains. Destruction or alteration of natural floodplains leads to greater flood risk.

This tool is designed to automatically discover global floodplain boundaries and access three different land use datasets. Based on these data, the tool does geospatial analytics to detect land use change during past years. **It is applicable anywhere in the world**.

Developed by **Qianjin Zheng** and **Adnan Rajib**

[Hydrology and Hydroinformatics Innovation (H2I) Lab](https://www.adnanrajib.com), University of Texas at Arlington

Contact: adnan.rajib@uta.edu

Please uncomment the following line each time before you run the tool for a new location (e.g., different locations). This action will delete the entire output folder of your previous work.

In [ ]:
# !rm -rf {out_dir}

### **Step 1**: Install Python Modules

In [ ]:
!pip install pyunpack wget rasterio patool fiona rioxarray googledrivedownloader pycrs
!pip install 'cdsapi>=0.7.2'

### **Step 2**: Import Python Modules

In [ ]:
import os, ee, glob, json, rioxarray, rasterio, cdsapi, fiona, shutil, xarray, wget, folium, pycrs, patoolib, pyunpack
import geemap as gee
from google.colab import files
from zipfile import ZipFile
import geopandas as gpd
import pandas as pd
import numpy as np
from rasterio.features import shapes
from osgeo import gdal
import rasterio.mask
from rasterio.plot import show
from rasterio.plot import show_hist
from rasterio.plot import plotting_extent
from ipyleaflet import Map, basemaps, basemap_to_tiles, DrawControl
from shapely.geometry import Polygon, mapping, shape
from google_drive_downloader import GoogleDriveDownloader as gdd
from branca.element import Template, MacroElement

### **Step 3**: Link your tool with Google Earth Engine

1. Before running this step, users should have an account setup in [Google Earth Engine](https://code.earthengine.google.com/register) using their own gmail ID.
2. Please replace your project ID or number (e.g.: h2i-lab) in the following code cell.

In [ ]:
gee.ee_initialize(project='ee-stella881210')

### **Step 4**: Specify the Names for Your Project and Output Folders

In [ ]:
file_name = input("""Please type in folder name (e.g. USCase) for your project without using any spaces:
""")
out_dir = '/content/%s_project'%file_name
os.makedirs(out_dir, exist_ok=True)

results_path = out_dir+'/FPLUC_results_%s'%file_name
os.makedirs(results_path, exist_ok=True)

Please type in folder name (e.g. USCase) for your project without using any spaces:
Asia


### **Step 5**: Define Functions

In [ ]:
def getAOI(option):
  global out_dir
  global uploaded
  if option==1:
    file_n = [fn.split(".")[0] for fn in uploaded.keys()][0]
    path = out_dir + '/%s.shp'%file_n
    if os.path.exists(path):
      aoi = path
      return aoi
    else: print("Your provided path is not valid!")
  elif option==2:
    drawn_feature = Map.draw_last_feature
    if drawn_feature is not None:
      bound = ee.FeatureCollection(drawn_feature)
      return bound
  else:
    print("Please select a option from [1, 2].")

def polygonized(Raster_path,shape_path):
  final_map = rioxarray.open_rasterio(Raster_path)
  mask = None
  with rasterio.Env():
      with rasterio.open(Raster_path) as src:
          image = src.read(1) # first band
          msk = src.read_masks(1)
          results = (
          {'properties': {'raster_val': v}, 'geometry': s}
          for i, (s, v)
          in enumerate(
              shapes(image, mask=msk, transform=src.transform))
          if v > 0)
  geoms = list(results)
  gpd_polygonized_raster = gpd.GeoDataFrame.from_features(geoms)
  gpd_polygonized_raster.crs = final_map.rio.crs
  gpd_polygonized_raster.to_file(shape_path)

def esc(code):
    return f'\033[{code}m'

def Rclip(shapef,rasterf,outf):
  with fiona.open(shapef, "r") as shapefile:
      shapes = [feature["geometry"] for feature in shapefile]
  with rasterio.open(rasterf) as src:
      out_image, out_transform = rasterio.mask.mask(src, shapes, crop=True)
      out_meta = src.meta
  out_meta.update({"driver": "GTiff",
                  "height": out_image.shape[1],
                  "width": out_image.shape[2],
                  "transform": out_transform})
  with rasterio.open(outf, "w", **out_meta) as dest:
      dest.write(out_image)

def CCI_CDS_download(yr,version_,path_name):
  dataset = "satellite-land-cover"
  request = {
      "variable": "all",
      "year": ["%s"%yr],
      "version": ["%s"%version_]
  }
  target = path_name
  client = cdsapi.Client()
  client.retrieve(dataset, request,target)

def unzip(out_dir,extension,fextension):
  for item in os.listdir(out_dir):
      if item.endswith(extension):
          file_name = os.path.basename(item)
          #print(file_name)
          with ZipFile(out_dir+"/%s"%file_name, 'r') as zipObject:
            listOfFileNames = zipObject.namelist()
            for fileName in listOfFileNames:
              if fileName.endswith(fextension):
                zipObject.extract(fileName, out_dir)

### **Step 6**: Upload or Select Your Location of Interest

In this section, you have two options to specify your location of interest:
1. If you wish to utilize your custom boundary shapefile, follow these steps:
  *   After running the code, click the **choose files** button
  *   Next, select your files **ALL AT THE SAME TIME** from your computer to upload them into Google Colab.
  *   Note: Allowed file extensions: shp, dbf, prj, shx, cpg, fix, qix, sbn or shp.xml.

2. If you do not have your own shapefile ready and you want to draw your location of interest, follow these steps:
  *   After running the code, navigate the map and
  zoom in to your desired location.
  *   Next, click on **"Draw a polygon" OR "Draw a rectangle"** on the left panel of the map.
  *   Finally, move your cursor to the desired location and draw rectangle or polygon on the map.

In [ ]:
option = int(input("""Please select following option (e.g.: 1 or 2):
1. You want to use your own shapefile of the specific region of interest;
2. You do NOT have your own shapefile
"""))

if option ==1:
  %cd {out_dir}
  uploaded = files.upload()
  while True:
    try:
      gdf = gpd.read_file(getAOI(option))
      break
    except:
      print("Files which you uploaded are invalid, please re-upload your shapefile")
      uploaded = files.upload()
  else:
    pass
else:
  Map = gee.Map(basemap='Esri.WorldTopoMap')
  gfplain250 = (ee.ImageCollection("projects/sat-io/open-datasets/GFPLAIN250")).mosaic()
  Map.addLayer(gfplain250,{"palette":["#002B4D"],"opacity":0.3},'Global Flood Plain 250m')
  display(Map)

Please select following option (e.g.: 1 or 2):
1. You want to use your own shapefile of the specific region of interest;
2. You do NOT have your own shapefile
1
/content/Asia_project


Saving Asia.cpg to Asia.cpg
Saving Asia.dbf to Asia.dbf
Saving Asia.prj to Asia.prj
Saving Asia.sbn to Asia.sbn
Saving Asia.sbx to Asia.sbx
Saving Asia.shp to Asia.shp
Saving Asia.shp.xml to Asia.shp.xml
Saving Asia.shx to Asia.shx


### **Step 7**: Extract Floodplain for Your Selected Location of Interest

The floodpain used in the default version of this tool covers all of the world. See the reference for more details.

Nardi et al. 2019. GFPLAIN250m, a global high-resolution dataset of Earth’s floodplains. Sci Data 6, 180309, https://doi.org/10.1038/sdata.2018.309

In [ ]:
if option == 1:
  path_shapefile = getAOI(option)
  bound = gee.shp_to_ee(path_shapefile)
  bound2 = bound.geometry()

else:
  bound2 = Map.draw_last_feature.geometry()
  bound = ee.FeatureCollection(getAOI(option))
  path_shapefile = out_dir+"/bound.shp"
  gee.ee_to_shp(bound, filename=path_shapefile)

Study_Area = gpd.read_file(path_shapefile)
bounds = Study_Area.to_crs(epsg='4326').bounds
lat_slice = slice(bounds.iloc[0]['maxy'],bounds.iloc[0]['miny'])
lon_slice = slice(bounds.iloc[0]['minx'],bounds.iloc[0]['maxx'])

fp = (
    ee.ImageCollection("projects/sat-io/open-datasets/GFPLAIN250")
    .filterBounds(bound)
    .mosaic()
    .clip(bound)
    .remap([0],[1])
    .rename("Floodplain")
    )

gee.ee_export_image(
    fp, filename=results_path+'/floodplain.tif', scale=250, region=bound2,unmask_value=0
)

ds = gdal.Open(results_path+'/floodplain.tif')
myarray = np.array(ds.GetRasterBand(1).ReadAsArray())
values = np.unique(myarray)
if np.any(values == 1):
  polygonized(Raster_path = results_path+'/floodplain.tif',
              shape_path = results_path+"/floodplain.shp")
else:
  print(esc('31;1;4') + 'NOTE:'+ esc(0))
  print("""There is no floodplain in the region of your interest.
           Please re-run the tool from the beginning.""")

Generating URL ...
Please wait ...
Data downloaded to /content/Asia_project/FPLUC_results_Asia/floodplain.tif


### **Step 8**: Download and Extract Land Use Dataset for the Selected Area

Reproject the selected boundary to match the spatial coordinate system of the land use layer

In [ ]:
USBound_pro = Study_Area.to_crs(epsg=5070)
USBound_pro.to_file(out_dir+"/Albers_boundary.shp")

fp = gpd.read_file(results_path+"/floodplain.shp")
fp_pro = fp.to_crs(epsg=5070)
fp_pro.to_file(out_dir+"/Albers_floodplain.shp")


The tool can automatically access three long term land use datasets. These datasets are generated from satellite remote sensing and simulation models. Two datasets are limited to the United States only while the third dataset is available for the entire globe. We named the three datasets respectively as the USGS data, NLCD data, and ESA data. See the following references.

References:

1. **[USGS data]** Sohl et al. 2018. Modeled historical land use and land cover for the conterminous United States: 1938-1992: USGS data release, https://doi.org/10.5066/F7KK99RR **[Use this if your study area is in the US]**

2. **[USGS data]** Sohl et al. 2018. Conterminous United States Land Cover Projections - 1992 to 2100: USGS data release, https://doi.org/10.5066/P95AK9HP
 **[Use this if your study area is in the US]**

3. **[NLCD data]** Homer et al. 2020. Conterminous United States land cover change patterns 2001–2016 from the 2016 National Land Cover Database, ISPRS Journal of Photogrammetry and Remote Sensing, (162) 184–199, https://doi.org/10.1016/j.isprsjprs.2020.02.019 **[Use this if your study area is in the US]**

4. **[ESA data]** ESA. 2017. Land Cover CCI Product User Guide Version 2. Tech. Rep, http://maps.elie.ucl.ac.be/CCI/viewer/download/ESACCI-LC-Ph2-PUGv2_2.0.pdf **[Use this if your study area is NOT in the US]**


**This tool can automatically access the new data (NLCD data and ESA data) whenever it is available on the source website.



In [ ]:
out_dir2 = '/content/supplement'
os.makedirs(out_dir2, exist_ok=True)

if not os.path.exists(out_dir2+'/CDS_download.zip'):
  gdd.download_file_from_google_drive(file_id='1zmG0RspADjk6uSNMc4DNjtpCPwjqpsjp',
                                      dest_path=out_dir2+'/CDS_download.zip',
                                      unzip=True)

shutil.copy2(out_dir2+"/CDS_download/.cdsapirc", "/root/.cdsapirc")
os.remove(out_dir2+'/CDS_download.zip')

if not os.path.exists(out_dir2+'/USGS_lookup_table.zip'):
    gdd.download_file_from_google_drive(file_id='1C_0bSvaPMj_7u3qhNitBQUb-F0mOPxRs',
                                      dest_path=out_dir2+'/USGS_lookup_table.zip',
                                      unzip=True)

Unzipping...Done.


In [ ]:
LULC = int(input("""Please use following options to select the Land Use products(e.g.: 1, or 2, or 3):
1. USGS data;
2. NLCD data;
3. ESA data
"""))

if LULC == 1:
  initial_year1 = str(input("Select inital year (from 1941 to 2000): "))
  final_year1 = str(input("Select final year (from 1941 to 2000): "))
  initial_year = initial_year1
  final_year = final_year1
  data = pd.read_csv(out_dir2+'/USGS_lookup_table.csv')
  for i in range(len(data)):
    if initial_year1 == str(data.Year[i]):
      url_USGS1 = data.Link[i]
      wget.download(url_USGS1,out=out_dir+"/%s.tif"%initial_year1)
    elif final_year1 == str(data.Year[i]):
      url_USGS2 = data.Link[i]
      wget.download(url_USGS2,out=out_dir+"/%s.tif"%final_year1)
    else:
      pass

  bound_path2 = out_dir+"/Albers_floodplain.shp"
  USGS_initial = out_dir+"/%s.tif"%initial_year1
  out1_path = out_dir+"/landuse_initial.tif"
  Rclip(shapef=bound_path2,rasterf=USGS_initial,outf=out1_path)
  USGS_final = out_dir+"/%s.tif"%final_year1
  out2_path = out_dir+"/landuse_final.tif"
  Rclip(shapef=bound_path2,rasterf=USGS_final,outf=out2_path)

  for file0 in glob.glob(out_dir+"/landuse*.tif"):
    print(file0)
    file_name = os.path.basename(file0).split(".")[0]
    with rasterio.open(file0) as src:
        array = src.read()
        array[np.where(array == 1)] = 1
        array[np.where(array == 2)] = 2
        array[np.where(array == 3)] = 2
        array[np.where(array == 4)] = 2
        array[np.where(array == 5)] = 2
        array[np.where(array == 6)] = 2
        array[np.where(array == 7)] = 3
        array[np.where(array == 8)] = 4
        array[np.where(array == 9)] = 4
        array[np.where(array == 10)] = 4
        array[np.where(array == 11)] = 5
        array[np.where(array == 12)] = 5
        array[np.where(array == 13)] = 6
        array[np.where(array == 14)] = 5
        array[np.where(array == 15)] = 7
        array[np.where(array == 16)] = 7
        array[np.where(array == 17)] = 1
        out_meta = src.meta
        out_meta.update({
            "nodata": 0})
    with rasterio.open(out_dir+"/%s_reclass.tif"%file_name, 'w', **out_meta) as dst:
        dst.write(array)

elif LULC == 2:
  initial_year2 = str(input("Select initial year (Use following option: 2021, 2019, 2016, 2013, 2011, 2008, 2006, 2004, 2001): "))
  final_year2 = str(input("Select final year (Use following option: 2021, 2019, 2016, 2013, 2011, 2008, 2006, 2004, 2001): "))
  initial_year = initial_year2
  final_year = final_year2
  url_NLCD1 = 'https://s3-us-west-2.amazonaws.com/mrlc/nlcd_'+initial_year2+'_land_cover_l48_20210604.zip'
  wget.download(url_NLCD1,out=out_dir+"/nlcd_%s_land_cover_l48_20210604.zip"%initial_year2)
  url_NLCD2 = 'https://s3-us-west-2.amazonaws.com/mrlc/nlcd_'+final_year2+'_land_cover_l48_20210604.zip'
  wget.download(url_NLCD2,out=out_dir+"/nlcd_%s_land_cover_l48_20210604.zip"%final_year2)

  unzip(out_dir=out_dir,extension='.zip',fextension='.img')
  unzip(out_dir=out_dir,extension='.zip',fextension='.ige')

  bound_path2 = out_dir+"/Albers_floodplain.shp"
  NLCD_initial = out_dir+'/nlcd_'+initial_year2+'_land_cover_l48_20210604.img'
  out1_path = out_dir+"/landuse_initial.tif"
  Rclip(shapef=bound_path2,rasterf=NLCD_initial,outf=out1_path)
  NLCD_final = out_dir+'/nlcd_'+final_year2+'_land_cover_l48_20210604.img'
  out2_path = out_dir+"/landuse_final.tif"
  Rclip(shapef=bound_path2,rasterf=NLCD_final,outf=out2_path)

  for file in glob.glob(out_dir+'/nlcd*'):
    os.remove(file)

  for file2 in glob.glob(out_dir+"/landuse*.tif"):
    print(file2)
    file_name1 = os.path.basename(file2).split(".")[0]

    with rasterio.open(file2) as src:
        array = src.read()
        array[np.where(array == 11)] = 1
        array[np.where(array == 12)] = 1
        array[np.where(array == 21)] = 2
        array[np.where(array == 22)] = 2
        array[np.where(array == 23)] = 2
        array[np.where(array == 24)] = 2
        array[np.where(array == 31)] = 3
        array[np.where(array == 41)] = 4
        array[np.where(array == 42)] = 4
        array[np.where(array == 43)] = 4
        array[np.where(array == 51)] = 5
        array[np.where(array == 52)] = 5
        array[np.where(array == 71)] = 5
        array[np.where(array == 81)] = 6
        array[np.where(array == 82)] = 6
        array[np.where(array == 90)] = 7
        array[np.where(array == 95)] = 7
        out_meta = src.meta
        out_meta.update({
          "nodata": 0})
    with rasterio.open(out_dir+"/%s_reclass.tif"%file_name1, 'w', **out_meta) as dst:
        dst.write(array)

else:
  initial_year3 = str(input("Select initial year (from 1992 to present): "))
  final_year3 = str(input("Select final year (from 1992 to present): "))
  initial_year = initial_year3
  final_year = final_year3
  year_lst = [initial_year3,final_year3]
  for year in year_lst:
    if int(year) < 2016:
      CCI_CDS_download(yr=year,version_='v2_0_7cds',path_name=out_dir2+'/download_%s.zip'%year)
      shutil.unpack_archive(out_dir2+'/download_%s.zip'%year, out_dir2)
      file = out_dir2+'/ESACCI-LC-L4-LCCS-Map-300m-P1Y-%s-v2.0.7cds.nc'%year
      out_cci = '%s/landuse_%s.tif'%(out_dir,year)
      ds = xarray.open_dataset(file)
      ds = ds.sel(lat=lat_slice,lon=lon_slice)["lccs_class"]
      ds.rio.write_crs("epsg:4326", inplace=True)
      ds.rio.to_raster(out_cci)
      ds = None
      os.remove(out_dir2+'/download_%s.zip'%year)
      os.remove(file)
    else:
      CCI_CDS_download(yr=year,version_='v2_1_1',path_name=out_dir2+'/download_%s.zip'%year)
      shutil.unpack_archive(out_dir2+'/download_%s.zip'%year, out_dir2)
      file = out_dir2+'/C3S-LC-L4-LCCS-Map-300m-P1Y-%s-v2.1.1.nc'%year
      out_cci = '%s/landuse_%s.tif'%(out_dir,year)
      ds = xarray.open_dataset(file)
      ds = ds.sel(lat=lat_slice,lon=lon_slice)["lccs_class"]
      ds.rio.write_crs("epsg:4326", inplace=True)
      ds.rio.to_raster(out_cci)
      ds = None
      os.remove(out_dir2+'/download_%s.zip'%year)
      os.remove(file)

  bound_path2 = results_path+"/floodplain.shp"
  CCI_initial = out_dir+'/landuse_%s.tif'%initial_year3
  out1_path = out_dir+"/landuse_initial.tif"
  Rclip(shapef=bound_path2,rasterf=CCI_initial,outf=out1_path)
  os.remove(CCI_initial)
  CCI_final = out_dir+'/landuse_%s.tif'%final_year3
  out2_path = out_dir+"/landuse_final.tif"
  Rclip(shapef=bound_path2,rasterf=CCI_final,outf=out2_path)
  os.remove(CCI_final)

  for file4 in glob.glob(out_dir+"/landuse*.tif"):
    print(file4)
    file_name3 = os.path.basename(file4).split(".")[0]
    with rasterio.open(file4) as src:
        array = src.read()
        profile = src.profile

        array[np.where(array == 10)] = 6
        array[np.where(array == 11)] = 6
        array[np.where(array == 12)] = 6
        array[np.where(array == 20)] = 6
        array[np.where(array == 30)] = 6
        array[np.where(array == 40)] = 6
        array[np.where(array == 50)] = 4
        array[np.where(array == 60)] = 4
        array[np.where(array == 61)] = 4
        array[np.where(array == 62)] = 4
        array[np.where(array == 70)] = 4
        array[np.where(array == 71)] = 4
        array[np.where(array == 72)] = 4
        array[np.where(array == 80)] = 4
        array[np.where(array == 81)] = 4
        array[np.where(array == 82)] = 4
        array[np.where(array == 90)] = 4
        array[np.where(array == 100)] = 4
        array[np.where(array == 110)] = 5
        array[np.where(array == 120)] = 5
        array[np.where(array == 121)] = 5
        array[np.where(array == 122)] = 5
        array[np.where(array == 130)] = 5
        array[np.where(array == 140)] = 5
        array[np.where(array == 150)] = 5
        array[np.where(array == 151)] = 5
        array[np.where(array == 152)] = 5
        array[np.where(array == 153)] = 5
        array[np.where(array == 160)] = 4
        array[np.where(array == 170)] = 4
        array[np.where(array == 180)] = 7
        array[np.where(array == 190)] = 2
        array[np.where(array == 200)] = 3
        array[np.where(array == 201)] = 3
        array[np.where(array == 202)] = 3
        array[np.where(array == 210)] = 1
        array[np.where(array == 220)] = 1
    with rasterio.open(out_dir+"/%s_reclass.tif"%file_name3, 'w', **profile) as dst:
        dst.write(array)

Please use following options to select the Land Use products(e.g.: 1, or 2, or 3):
1. USGS data;
2. NLCD data;
3. ESA data
3
Select initial year (from 1992 to present): 1992
Select final year (from 1992 to present): 2020


2024-10-31 22:53:49,111 WARNING [2024-10-30T00:00:00] System is having technical problems on its adaptor for accessing external URLs. Some requests might randomnly fail. We are working to resume operations asap.
2024-10-31 22:53:49,116 INFO [2024-09-28T00:00:00] **Welcome to the New Climate Data Store (CDS)!** This new system is in its early days of full operations and still undergoing enhancements and fine tuning. Some disruptions are to be expected. Your 
[feedback](https://jira.ecmwf.int/plugins/servlet/desk/portal/1/create/202) is key to improve the user experience on the new CDS for the benefit of everyone. Thank you.
INFO:cads_api_client.legacy_api_client:[2024-09-28T00:00:00] **Welcome to the New Climate Data Store (CDS)!** This new system is in its early days of full operations and still undergoing enhancements and fine tuning. Some disruptions are to be expected. Your 
[feedback](https://jira.ecmwf.int/plugins/servlet/desk/portal/1/create/202) is key to improve the user experi

f1a5d05fef9ccb3bd63ef1ffc066bfe9.zip:   0%|          | 0.00/2.15G [00:00<?, ?B/s]

2024-10-31 22:59:27,573 WARNING [2024-10-30T00:00:00] System is having technical problems on its adaptor for accessing external URLs. Some requests might randomnly fail. We are working to resume operations asap.
2024-10-31 22:59:27,577 INFO [2024-09-28T00:00:00] **Welcome to the New Climate Data Store (CDS)!** This new system is in its early days of full operations and still undergoing enhancements and fine tuning. Some disruptions are to be expected. Your 
[feedback](https://jira.ecmwf.int/plugins/servlet/desk/portal/1/create/202) is key to improve the user experience on the new CDS for the benefit of everyone. Thank you.
INFO:cads_api_client.legacy_api_client:[2024-09-28T00:00:00] **Welcome to the New Climate Data Store (CDS)!** This new system is in its early days of full operations and still undergoing enhancements and fine tuning. Some disruptions are to be expected. Your 
[feedback](https://jira.ecmwf.int/plugins/servlet/desk/portal/1/create/202) is key to improve the user experi

933d9a4da459118785f658b613f1ba36.zip:   0%|          | 0.00/2.18G [00:00<?, ?B/s]

/content/Asia_project/landuse_initial.tif
/content/Asia_project/landuse_final.tif


### **Step 9**: Do Geospatial Analysis to Identify Land Use Change within Your Floodplain Boundary

In [ ]:
initial_path = out_dir+"/landuse_initial_reclass.tif"
with rasterio.open(initial_path) as initial:
    initial_im = initial.read(1, masked=True)
    initial_ext = rasterio.plot.plotting_extent(initial)
    bounds = plotting_extent(initial)
final_path = out_dir+"/landuse_final_reclass.tif"
with rasterio.open(final_path) as final:
    final_im = final.read(1, masked=True)
    dsm_meta = final.profile

Calculate the difference between two rasters

In [ ]:
diff = final_im - initial_im
with rasterio.open(out_dir+"/Difference_Map.tif", 'w', **dsm_meta) as ff:
    ff.write(diff,1)

with rasterio.open(out_dir+'/Difference_Map.tif') as src:
    array = src.read()
    array[np.where((array > 0)&(array<249))] = 2
    array[np.where(array>249)] = 255
    array[np.where(array==0)] = 255
    out_meta = src.meta
    out_meta.update({
             "nodata": 255})
with rasterio.open(results_path+'/Final_Map.tif', 'w', **out_meta) as dst:
    dst.write(array)

ds = gdal.Open(results_path+'/Final_Map.tif')
myarray = np.array(ds.GetRasterBand(1).ReadAsArray())
values = np.unique(myarray)
if np.any(values == 2):
  pass
else:
  print('\033[1m'  +"""There has been no land use change in the region of your interest during your study period.
You can start a new project with a different location and time range."""+'\033[0m')

### **Step 10**: Mapping Change VS No Change Results


In [ ]:
with rasterio.open(results_path+'/floodplain.tif') as src:
  data = src.read(1)
count_FP = np.sum(data == 1)
AFP = count_FP*0.25*0.25
with rasterio.open(results_path+"/Final_Map.tif") as src:
  data = src.read(1)
count = np.sum(data == 2)
AChange = count*0.25*0.25
precentageC = AChange/AFP * 100

city_gjson = Study_Area.to_crs(epsg='4326').to_json()
floodplain_file = results_path+"/floodplain.shp"
floodplain_gdf = gpd.read_file(floodplain_file)
floodplain_gjson = floodplain_gdf.to_crs(epsg='4326').to_json()
polygonized(Raster_path = results_path+'/Final_Map.tif', shape_path = out_dir+"/Final_Map.shp")
final_map = out_dir+"/Final_Map.shp"
final_map_gdf = gpd.read_file(final_map)
final_map_gjson = final_map_gdf.to_crs(epsg='4326').to_json()
bounds = Study_Area.to_crs(epsg='4326').bounds
coords = bounds.iloc[0]
lat = (coords['miny'] + coords['maxy']) / 2
lon = (coords['minx'] + coords['maxx']) / 2
m = folium.Map(location=[lat, lon], zoom_start = 8, tiles="cartodb positron")

heading = 'Summary of Analysis:'
paragraph_line1 = "Total floodplain area selected is <b>%s</b> squre kilometer (km^2)."%str(round(AFP, 2))
paragraph_line2 = "Total area of land use change within your selected floodplain is <b>%s</b> squre kilometer (km^2)."%str(round(AChange, 2))
paragraph_line3 = "The percentage change in land use within the floodplain is: <b>%s%%</b> between %s and %s."%(str(round(precentageC, 2)),initial_year,final_year)
header_size = "20px"
paragraph = f"{paragraph_line1}<br>{paragraph_line2}<br>{paragraph_line3}"

legend_html = '''
<div style="position: fixed; bottom: 50px; left: 50px;
            z-index:9999; background-color: white;
            border: 1px solid grey; padding: 10px;
            font-size: 14px;border-radius: 5px;
            ">
    <div style="width: 100%; text-align: center; font-weight: bold;">Legend</div>
    <hr style="margin: 5px 0;">
    <div style="display: flex; align-items: center;">
        <div style="width: 20px; height: 20px; background-color: red; margin-right: 10px;"></div>
        Land Use Change
    </div>
    <div style="display: flex; align-items: center; margin-top: 5px;">
        <div style="width: 20px; height: 20px; background-color: blue; margin-right: 10px;"></div>
        Floodplain
    </div>
</div>
'''

title_html = f'''
{{% macro html(this, kwargs) %}}
<style>
  .map-title {{
      position: absolute; top: 10px;left: 50px;
      z-index: 9999;background-color: white;padding: 10px;
      border-radius: 5px;box-shadow: 3px 3px 5px rgba(0,0,0,0.3);font-size: 15px;
  }}
  .map-title h1 {{
      font-size: {header_size};font-weight: bold;  color: red;
  }}
  .map-title p {{
      font-size: 15px;
  }}
</style>
<div class="map-title">
    <h1>{heading}</h1>
    <p>{paragraph}</p>
</div>
{{% endmacro %}}
'''

template = Template(title_html)
macro = MacroElement()
macro._template = template

style_city = {'fillColor':'#050505','color':'#050505','fillOpacity': 0}
style_fp = {'fillOpacity': 0.3}
style_results = {'color':'#FF0000',"fillOpacity": 1.0}
city = folium.features.GeoJson(city_gjson,  name='Boundary', style_function = lambda x:style_city)
floodplain = folium.features.GeoJson(floodplain_gjson,
                                     name='floodplain',
                                     style_function = lambda x:style_fp,
                                     tooltip=folium.features.GeoJsonTooltip(fields=['raster_val'],
                                                                         aliases=['Floodplain Extent'],
                                                                         style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")))

results = folium.features.GeoJson(final_map_gjson,
                                  name='Change VS No Change',
                                  style_function = lambda x:style_results,
                                  tooltip=folium.features.GeoJsonTooltip(fields=['raster_val'],
                                                                         aliases=['Change of land use between two points in time'],
                                                                         style=("background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;")))



m.get_root().add_child(macro)
m.get_root().html.add_child(folium.Element(legend_html))
m.add_child(city)
m.add_child(floodplain)
m.add_child(results)
m.add_child(folium.LatLngPopup())
m.add_child(folium.LayerControl())
m

### **Step 11**: Download the Results to Your Local Computer

In [ ]:
m.save(results_path +"/CNC_Map.html")
shutil.copy(out_dir+'/landuse_final_reclass.tif', results_path+'/landuse_final.tif')
shutil.copy(out_dir+'/landuse_initial_reclass.tif', results_path+'/landuse_initial.tif')

base_name = results_path
format = 'zip'
root_dir = out_dir
base_dir = "./%s"%(results_path.split('/')[-1])
shutil.make_archive(base_name,format,root_dir,base_dir)

'/content/TX_project/FPLUC_results_TX.zip'

In [ ]:
files.download('%s.zip'%results_path)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>